In [1]:
# !pip install -q "monai-weekly[nibabel, matplotlib]"

In [2]:
# For volume visualization
# !pip install -q plotly

In [3]:
import argparse
import os
import sys
import time
import warnings

# Suppress most warnings for cleaner logs (comment out if debugging is needed)
warnings.filterwarnings("ignore")

import torch
import torch.nn.functional as F
import torch.optim as optim
from tqdm import tqdm

from torch.utils.tensorboard import SummaryWriter

#---------added part--------
import SimpleITK as sitk # read .mha
import numpy as np
np.random.seed(0)
import glob
from torch.utils.data import Dataset, DataLoader



In [4]:
class MhaDataset(Dataset):
    """ for full dataset """
    def __init__(self, root_dir, transform=None):
        self.root_dir = root_dir
        self.sample_dirs = sorted(glob.glob(os.path.join(root_dir, "1HN*"))) # list of all sibdor in root_dir
        self.transform = transform
    def __len__(self):
        return len(self.sample_dirs)
    def __getitem__(self, idx): # full image
        d = self.sample_dirs[idx]
        ct_path   = os.path.join(d, "ct.mha")
        mri_path  = os.path.join(d, "mr.mha")
        mask_path = os.path.join(d, "mask.mha")

        type_map = {
            'AB': int(0),
            'HN': int(1),
            'TH': int(2)
        }
        lbl = type_map.get(self.root_dir.split('/')[-1], int(-1))
        if lbl == -1:
            raise ValueError(f"Unknown label for directory {self.root_dir}")
        # see test1.ipynb to learn more about 'sitk'
        ct_arr   = sitk.GetArrayFromImage(sitk.ReadImage(ct_path)).astype(np.float32)
        mask_arr = sitk.GetArrayFromImage(sitk.ReadImage(mask_path)).astype(np.float32)
        mri_arr  = sitk.GetArrayFromImage(sitk.ReadImage(mri_path)).astype(np.float32)

        ct_tensor   = torch.from_numpy(ct_arr)
        mask_tensor = torch.from_numpy(mask_arr)
        mri_tensor  = torch.from_numpy(mri_arr)
        class_tensor= torch.tensor(lbl, dtype=torch.long)
        if self.transform:
            ct_tensor, mask_tensor = self.transform(ct_tensor, mask_tensor)
        return {
            "ct": ct_tensor,
            "mri":  mri_tensor,
            "masks":  mask_tensor,
            "classes": class_tensor,
        }
 

In [5]:
class MhaDataset_small(Dataset):
    """ on small dataset """
    def __init__(self, root_dir, transform=None, n_images=4, n_patches=50, patch_size=(16,128,128)): #(16,64,64)
        self.n_patches = n_patches
        n_max = len(glob.glob(os.path.join(root_dir, "1HN*")))
        self.n_images = min(n_images, n_max)
        self.sample_dirs = sorted(glob.glob(os.path.join(root_dir, "1HN*"))) [:self.n_images]
        self.transform = transform
        self.patch_size = patch_size
        
        # NOTE: since the sampling data is small, we will do the preprocessing here
        self.ct_arrs = []
        self.mask_arrs = []
        self.mri_arrs = []
        self.lbls = []
        self.ct_maxs = []
        self.ct_mins = []
        self.mri_maxs = []
        
        for d in self.sample_dirs:
            ct_path   = os.path.join(d, "ct.mha")
            mri_path  = os.path.join(d, "mr.mha")
            mask_path = os.path.join(d, "mask.mha")
            # determine 1-hot class ~ anatomy
            if root_dir.split('/')[-1] == 'AB':
                lbl = np.array([1, 0, 0])
            elif root_dir.split('/')[-1] == 'HN':
                lbl = np.array([0, 1, 0])
            elif root_dir.split('/')[-1] == 'TH':
                lbl = np.array([0, 0, 1])
                
            # path -> image -> reorient to RAS -> numpy array
            ct_arr   = sitk.GetArrayFromImage(
                self.reorient_to_RAS(sitk.ReadImage(ct_path))
                ).astype(np.float32)
            mask_arr = sitk.GetArrayFromImage(
                self.reorient_to_RAS(sitk.ReadImage(mask_path))
                ).astype(np.float32)
            mri_arr  = sitk.GetArrayFromImage(
                self.reorient_to_RAS(sitk.ReadImage(mri_path))
                ).astype(np.float32)
            
            # save original information for later use
            ct_max = np.max(ct_arr)
            ct_min = np.min(ct_arr)
            mri_max = np.max(mri_arr)
            
            # ct clip to -1000, 3000 and normalize to 0,1
            ct_arr = np.clip(ct_arr, -1000, 3000)
            ct_arr = (ct_arr + 1000) / 4000
            # mri clip to 0, np.max and normalize to 0, 1
            mri_arr = np.clip(mri_arr, 0, np.max(mri_arr))
            mri_arr = (mri_arr - np.min(mri_arr)) / (np.max(mri_arr) - np.min(mri_arr))
            
            # crop random patch
            for j in range(self.n_patches):
                # extract random patch
                start_h, start_w, start_d = self.extract_random_patch(ct_arr.shape, self.patch_size)
                ct_arr   = ct_arr[start_h:start_h+self.patch_size[0], start_w:start_w+self.patch_size[1], start_d:start_d+self.patch_size[2]]
                mask_arr = mask_arr[start_h:start_h+self.patch_size[0], start_w:start_w+self.patch_size[1], start_d:start_d+self.patch_size[2]]
                mri_arr  = mri_arr[start_h:start_h+self.patch_size[0], start_w:start_w+self.patch_size[1], start_d:start_d+self.patch_size[2]]
            
                # add to list
                self.ct_arrs.append(ct_arr)
                self.mask_arrs.append(mask_arr)
                self.mri_arrs.append(mri_arr)
                self.lbls.append(lbl)
                
                self.ct_maxs.append(ct_max)
                self.ct_mins.append(ct_min)
                self.mri_maxs.append(mri_max)

    def __len__(self):
        return len(self.sample_dirs)
    def __getitem__(self, idx): # full image
        ct_arr   = self.ct_arrs[idx]
        mask_arr = self.mask_arrs[idx]
        mri_arr  = self.mri_arrs[idx]
        lbl      = self.lbls[idx]

        ct_tensor   = torch.from_numpy(ct_arr).unsqueeze(0) # [1, D, H, W] [channel, patch_size]
        mask_tensor = torch.from_numpy(mask_arr).unsqueeze(0) # [1, D, H, W] [channel, patchsize]
        mri_tensor  = torch.from_numpy(mri_arr).unsqueeze(0)
        class_tensor= torch.tensor(lbl, dtype=torch.long)
        if self.transform:
            ct_tensor, mask_tensor = self.transform(ct_tensor, mask_tensor)
        return {
            "images": ct_tensor,
            "masks":  mri_tensor,
            "masks_":  mask_tensor,
            "classes": class_tensor,
            "ct_max": self.ct_maxs[idx],
            "ct_min": self.ct_mins[idx],
            "mri_max": self.mri_maxs[idx],
        }
    # helper functions
    def reorient_to_RAS(self, img: sitk.Image) -> sitk.Image:
        """
        Take any SimpleITK Image (in LPS, RAS, whatever) and
        return an image whose axes are labeled R,A,S.
        """
        dicom_orient = sitk.DICOMOrientImageFilter()
        dicom_orient.SetDesiredCoordinateOrientation("RAS")  # target orientation
        return dicom_orient.Execute(img)

    def extract_random_patch(self, volume_shape, patch_size):
        """Extract a random patch of size patch_size from a 3D volume."""
        H, W, D = volume_shape
        ph, pw, pd = patch_size
        if H < ph or W < pw or D < pd:
            raise ValueError("Volume shape is smaller than patch size.")
        start_h = np.random.randint(0, H - ph + 1)
        start_w = np.random.randint(0, W - pw + 1)
        start_d = np.random.randint(0, D - pd + 1)
        # patch = volume[start_h:start_h+ph, start_w:start_w+pw, start_d:start_d+pd]
        # print(start_h, start_w, start_d)
        return start_h, start_w, start_d  # patch + its coordinates
    
    def show(self):
        """ return a dictionary of processed data"""
        return {'images': self.ct_arrs,
                'masks_': self.mask_arrs,
                'masks':self.mri_arrs,
                'ct_max': self.ct_maxs,
                'ct_min': self.ct_mins,
                'mri_max': self.mri_maxs,
                'classes': self.lbls,
                'n_data': f'{self.n_images} x {self.n_patches} = {self.n_images*self.n_patches}',
                'patch_size': self.patch_size,
        }

In [6]:
config = {
    "train_args": {
        "batch_size": 2,
    },
    "data_args": {
        "train_root": "./synthRAD2025_Task1_Train_D_small/Task1/HN",
        "val_root": "./synthRAD2025_Task1_Train_D/Task1/HN",
    }
}

# Read core settings from config
batch_size = config["train_args"]["batch_size"]   

# NOTE: new data loader
train_dataset = MhaDataset_small(root_dir=config["data_args"]["train_root"])
val_dataset   = MhaDataset_small(root_dir=config["data_args"]["val_root"])
train_loader  = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_loader    = DataLoader(val_dataset,   batch_size=batch_size, shuffle=False)



In [7]:
train_dataset[0]

{'images': tensor([[[[2.2775e-01, 2.2725e-01, 2.2825e-01,  ..., 1.0000e-03,
            1.0000e-03, 1.0000e-03],
           [2.3250e-01, 2.2850e-01, 2.3325e-01,  ..., 7.5000e-04,
            1.7500e-03, 1.5000e-03],
           [2.3100e-01, 2.3200e-01, 2.3775e-01,  ..., 1.0000e-03,
            1.5000e-03, 0.0000e+00],
           ...,
           [2.5075e-01, 2.5075e-01, 2.5275e-01,  ..., 1.0000e-03,
            2.5000e-04, 7.5000e-04],
           [2.5200e-01, 2.5200e-01, 2.5575e-01,  ..., 0.0000e+00,
            0.0000e+00, 0.0000e+00],
           [2.5450e-01, 2.5475e-01, 2.5375e-01,  ..., 0.0000e+00,
            1.2500e-03, 1.2500e-03]],
 
          [[2.2825e-01, 2.3425e-01, 2.3600e-01,  ..., 5.0000e-04,
            0.0000e+00, 0.0000e+00],
           [2.2650e-01, 2.3000e-01, 2.3600e-01,  ..., 7.5000e-04,
            7.5000e-04, 1.5000e-03],
           [2.2700e-01, 2.2675e-01, 2.3075e-01,  ..., 1.5000e-03,
            7.5000e-04, 5.0000e-04],
           ...,
           [2.5300e-01, 2.55

In [8]:
b = next(iter(train_loader))

In [9]:
b

{'images': tensor([[[[[2.2775e-01, 2.2725e-01, 2.2825e-01,  ..., 1.0000e-03,
             1.0000e-03, 1.0000e-03],
            [2.3250e-01, 2.2850e-01, 2.3325e-01,  ..., 7.5000e-04,
             1.7500e-03, 1.5000e-03],
            [2.3100e-01, 2.3200e-01, 2.3775e-01,  ..., 1.0000e-03,
             1.5000e-03, 0.0000e+00],
            ...,
            [2.5075e-01, 2.5075e-01, 2.5275e-01,  ..., 1.0000e-03,
             2.5000e-04, 7.5000e-04],
            [2.5200e-01, 2.5200e-01, 2.5575e-01,  ..., 0.0000e+00,
             0.0000e+00, 0.0000e+00],
            [2.5450e-01, 2.5475e-01, 2.5375e-01,  ..., 0.0000e+00,
             1.2500e-03, 1.2500e-03]],
 
           [[2.2825e-01, 2.3425e-01, 2.3600e-01,  ..., 5.0000e-04,
             0.0000e+00, 0.0000e+00],
            [2.2650e-01, 2.3000e-01, 2.3600e-01,  ..., 7.5000e-04,
             7.5000e-04, 1.5000e-03],
            [2.2700e-01, 2.2675e-01, 2.3075e-01,  ..., 1.5000e-03,
             7.5000e-04, 5.0000e-04],
            ...,
        

In [10]:
len(train_loader)

2

In [11]:
from monai.visualize import matshow3d, plot_2d_or_3d_image, add_animated_gif

In [12]:
fig, img_grid = matshow3d(
    volume=b['images'][1],
    fig=None,
    title="input image",
    figsize=(100, 100),
    every_n=1,
    frame_dim=0,
    show=True,
    cmap="gray",
)

In [13]:
output_dir ='./logs'
tb_dir = os.path.join(output_dir, "prepare_data")

In [ ]:
writer = SummaryWriter(log_dir=tb_dir)
writer.add_image('grid', img_grid[np.newaxis], 0)
plot_2d_or_3d_image(data=b['images'][0], step=0, writer=writer, frame_dim=0)
add_animated_gif(writer, 'animated', b['images'][0], frame_dim=1, scale_factor=255)
writer.close()

In [18]:
%load_ext tensorboard
%tensorboard --logdir=$output_dir

Reusing TensorBoard on port 6008 (pid 19816), started 1:52:59 ago. (Use '!kill 19816' to kill it.)

In [19]:
import plotly.graph_objects as go
import numpy as np
values = b['images'][1][0]
Z, X, Y = np.mgrid[0:values.shape[0], 0:values.shape[1], 0:values.shape[2]]

fig = go.Figure(data=go.Volume(
    x=X.flatten(),
    y=Y.flatten(),
    z=Z.flatten(),
    value=values.flatten(),
    isomin=0.1,
    isomax=values.max().item(),
    opacity=0.2, # needs to be small to see through all surfaces
    surface_count=21, # needs to be a large number for good volume rendering
    ))
fig.show()